In [ ]:
#https://github.com/allenai/bilm-tf

In [2]:
import re
import pandas as pd
import numpy as np
from time import time
import os
from collections import Counter

In [6]:
data_train = pd.read_csv("/home/mahmoud/Desktop/Tunisian Dialect Language Model TDLM/corpus/corpus.txt",
                         header=None,sep='\n',error_bad_lines=False)
data_train.columns = ["text"]
data_train["text"] = data_train["text"].apply(str)
data_train["text"] = data_train["text"].str.lower()
print("Shape of training data = ", data_train.shape)
data_train.sample(10)

Shape of training data =  (52603, 1)


b'Skipping line 29: expected 1 fields, saw 2\nSkipping line 259: expected 1 fields, saw 2\nSkipping line 6339: expected 1 fields, saw 2\nSkipping line 6341: expected 1 fields, saw 2\nSkipping line 6342: expected 1 fields, saw 2\nSkipping line 6636: expected 1 fields, saw 2\nSkipping line 7431: expected 1 fields, saw 2\nSkipping line 7536: expected 1 fields, saw 2\nSkipping line 7537: expected 1 fields, saw 2\nSkipping line 7687: expected 1 fields, saw 2\nSkipping line 7917: expected 1 fields, saw 2\nSkipping line 8387: expected 1 fields, saw 2\nSkipping line 8972: expected 1 fields, saw 2\nSkipping line 9963: expected 1 fields, saw 2\nSkipping line 13698: expected 1 fields, saw 2\nSkipping line 13703: expected 1 fields, saw 2\nSkipping line 14709: expected 1 fields, saw 2\nSkipping line 14812: expected 1 fields, saw 2\nSkipping line 14847: expected 1 fields, saw 2\nSkipping line 14879: expected 1 fields, saw 2\nSkipping line 15018: expected 1 fields, saw 2\nSkipping line 15036: expecte

text
26314                               تنجم تورني هذي يعيشك
16614               بيتك هي اربعه و خمسين تلاثه و تلاثين
5630   عندي برشا ما تفرجتش في حصه راقيه كيما اليله بر...
7239                     وانا نقومو من الموت يوم القيامه
29545                             شنيه المعالم في الطريق
6606                                              متي 20
24848                                             سامحني
10120  ذكر ولا انثي علي خاطركم الكلكم واحد في المسيح ...
45907                                         bravo sami
44217                                               tfoh

In [7]:
data_train['transcript'] = data_train['text'] + " ."
data_train['transcript'].head()

0    يا سيدي علي عيشوشه واله تمثل مليح وتمثيلها مقنع .
1    امنه تصلح وزيره مراه عالاقل تعطي منظر باهي لتو...
2                                 حنان الشقراني احسن .
3                                           بري روحي .
4                                       معلم يا لطفي .
Name: transcript, dtype: object

In [8]:
#As the training requires multiple files with one text sentence per line, we will create 20K training files 
#by writing 6 sentences per file. After running the below python snippet, 
#we get 20K files in train directory.
data_train.shape

(52603, 2)

In [9]:
if not os.path.exists("swb/train"):
    os.makedirs("swb/train")
 
for i in range(0,data_train.shape[0],6):
    text = "\n".join(data_train['transcript'][i:i+6].tolist())
    fp = open("swb/train/"+str(i)+".txt","w")
    fp.write(text)
    fp.close()

The vocabulary file is a a text file with one token per line. It must also include the special tokens <S>, </S> and <UNK> (case sensitive) in the file. The vocabulary file should be sorted in descending order by token count in your training data. The first three lines should be the special tokens (<S>, </S> and <UNK>), then the most common token in the training data, ending with the least common token.

In [10]:
texts = " ".join(data_train['transcript'].tolist())
words = texts.split(" ")
print("Number of tokens in Training data = ",len(words))

Number of tokens in Training data =  408846


In [11]:
dictionary = Counter(words)
print("Size of Vocab",len(dictionary))
sorted_vocab = ["<S>","</S>","<UNK>"] #["&lt;S&gt;","&lt;/S&gt;","&lt;UNK&gt;"]
sorted_vocab.extend([pair[0] for pair in dictionary.most_common()])
 

Size of Vocab 68904


In [12]:
text = "\n".join(sorted_vocab)
fp = open("swb/vocab.txt","w")
fp.write(text)
fp.close()

In [13]:
from bilm.training import train, load_options_latest_checkpoint, load_vocab

In [14]:
from bilm.data import BidirectionalLMDataset

In [15]:
import numpy as np

In [16]:
######################### train ELMO embedding ############################

In [17]:
 # load the vocab
vocab = load_vocab('swb/vocab.txt', 50)

In [18]:
# define the options
batch_size = 32  # batch size for each GPU
n_gpus = 1

# number of tokens in training data (this for 1B Word Benchmark)
n_train_tokens = len(dictionary) #768648884

if not os.path.exists("swb/checkpoint"):
    os.makedirs("swb/checkpoint")
options = {
     'bidirectional': True,

     'char_cnn': {'activation': 'relu',
      'embedding': {'dim': 16},
      'filters': [[1, 32],
       [2, 32],
       [3, 64],
       [4, 128],
       [5, 256],
       [6, 512],
       [7, 1024]],
      'max_characters_per_token': 50,
      'n_characters': 261,
      'n_highway': 2},
    
     'dropout': 0.1,
    
     'lstm': {
      'cell_clip': 3,
      'dim': 4096,
      'n_layers': 2,
      'proj_clip': 3,
      'projection_dim': 512,
      'use_skip_connections': True},
    
     'all_clip_norm_val': 10.0,
    
     'n_epochs': 10,
     'n_train_tokens': n_train_tokens,
     'batch_size': batch_size,
     'n_tokens_vocab': vocab.size,
     'unroll_steps': 20,
     'n_negative_samples_batch': 8192,
    }

import json
with open('swb/checkpoint/options.json', 'w') as fp:
    json.dump(options, fp)

In [19]:
if not os.path.exists("swb/checkpoint"):
    os.makedirs("swb/checkpoint")
options = {
     'bidirectional': True,

     'char_cnn': {'activation': 'relu',
      'embedding': {'dim': 16},
      'filters': [[1, 32],
       [2, 32],
       [3, 64],
       [4, 128]],
      'max_characters_per_token': 50,
      'n_characters': 261,
      'n_highway': 2},
    
     'dropout': 0.2,
    
     'lstm': {
      'cell_clip': 3,
      'dim': 128,
      'n_layers': 2,
      'proj_clip': 3,
      'projection_dim': 64,
      'use_skip_connections': True},
    
     'all_clip_norm_val': 10.0,
    
     'n_epochs': 15,
     'n_train_tokens': n_train_tokens,
     'batch_size': batch_size,
     'n_tokens_vocab': vocab.size,
     'unroll_steps': 20,
     'n_negative_samples_batch': 192,#8192
    }

import json
with open('swb/checkpoint/options.json', 'w') as fp:
    json.dump(options, fp)

In [20]:
prefix = 'swb/train/*'
data = BidirectionalLMDataset(prefix, vocab, test=False,
                                      shuffle_on_load=True)

Found 8768 shards at swb/train/*
Loading data from: swb/train/9390.txt
Loaded 6 sentences.
Finished loading
Found 8768 shards at swb/train/*
Loading data from: swb/train/4272.txt
Loaded 6 sentences.
Finished loading


In [21]:
if not os.path.exists("swb/checkpoint"):
    os.makedirs("swb/checkpoint")
tf_save_dir = 'swb/checkpoint'
tf_log_dir = 'swb/checkpoint'


In [22]:
from time import time
t = time()

In [23]:
!export CUDA_VISIBLE_DEVICES=0

In [24]:
n_gpus

1

In [25]:
train(options, data, n_gpus, tf_save_dir, tf_log_dir)







Instructions for updating:
Use the `axis` argument instead
USING SKIP CONNECTIONS
Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.


Instructions for updating:
This class is equivalent as tf.keras.layers.StackedRNNCells, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.RNN(cell, unroll=True)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.

Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where

[['global_step:0', TensorShape([])],
 ['lm/CNN/W_cnn_0:0',
  TensorShape([Dimension(1), Dimension(1), Dimension(16), Dimension(32)])],



Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor



Instructions for updating:
Use `tf.global_variables_initializer` instead.



Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably safe to ignore.
'list' object has no attribute 'name'
Training for 15 epochs and 1605 batches
Loading data from: swb/train/35592.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/50400.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/21912.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/33744.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/4602.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/6696.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/546.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/29226.txt
Loaded 6 senten

Loading data from: swb/train/11028.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/37110.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/16416.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/13686.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/43026.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/11010.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/19992.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/37362.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/9966.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/27564.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/40050.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/13170.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/9030.txt
Loaded 6 sentences.
Finished loading
Loading data f

Loading data from: swb/train/36432.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/19056.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/31674.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/36924.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/52152.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/30366.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/444.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/14544.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/40560.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/5094.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/4962.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/31974.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/30408.txt
Loaded 6 sentences.
Finished loading
Loading data fro

Loading data from: swb/train/45456.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/23190.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/44226.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/47268.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/13974.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/39306.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/20484.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/31182.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/45984.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/27894.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/5730.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/30048.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/45024.txt
Loaded 6 sentences.
Finished loading
Loading data 

...

Loading data from: swb/train/51120.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/35922.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/13224.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/18894.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/21798.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/31992.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/15216.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/11574.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/8100.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/39372.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/20424.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/24720.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/34806.txt
Loaded 6 sentences.
Finished loading
Loading data 

Loading data from: swb/train/36270.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/46920.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/28212.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/28584.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/9324.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/30876.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/32946.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/30882.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/27558.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/6312.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/29736.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/44838.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/32790.txt
Loaded 6 sentences.
Finished loading
Loading data f

Loading data from: swb/train/9576.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/37032.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/43764.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/2046.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/46254.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/36024.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/6234.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/25890.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/41886.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/50574.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/45864.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/44874.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/18174.txt
Loaded 6 sentences.
Finished loading
Loading data fr

Loading data from: swb/train/32130.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/17712.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/45606.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/17478.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/9210.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/17424.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/2346.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/17202.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/22956.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/15726.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/19242.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/41538.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/48942.txt
Loaded 6 sentences.
Finished loading
Loading data f

Loading data from: swb/train/25278.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/16272.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/26250.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/21972.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/15894.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/8154.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/42540.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/8892.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/20496.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/11028.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/28782.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/30240.txt
Loaded 6 sentences.
Finished loading
Loading data from: swb/train/4260.txt
Loaded 6 sentences.
Finished loading
Loading data fr

In [26]:
print("elapsed time (s): ", time()-t)

elapsed time (s):  379.07420086860657


In [27]:
379/60


6.316666666666666

Convert Tf Checkpoint to hdf5

This step is important to convert the checkpoint model to hdf5 format which can be easily used for inference.



In [28]:
from bilm.training import dump_weights as dw

In [29]:
save_dir = 'swb/checkpoint'
outfile = 'swb/swb_weights.hdf5'

In [30]:
import tensorflow as tf
tf.reset_default_graph() 

In [31]:
dw(save_dir,outfile)

USING SKIP CONNECTIONS
INFO:tensorflow:Restoring parameters from swb/checkpoint/model.ckpt-1605
Saving variable lm/char_embed:0 with name char_embed
Saving variable lm/CNN/W_cnn_0:0 with name CNN/W_cnn_0
Saving variable lm/CNN/b_cnn_0:0 with name CNN/b_cnn_0
Saving variable lm/CNN/W_cnn_1:0 with name CNN/W_cnn_1
Saving variable lm/CNN/b_cnn_1:0 with name CNN/b_cnn_1
Saving variable lm/CNN/W_cnn_2:0 with name CNN/W_cnn_2
Saving variable lm/CNN/b_cnn_2:0 with name CNN/b_cnn_2
Saving variable lm/CNN/W_cnn_3:0 with name CNN/W_cnn_3
Saving variable lm/CNN/b_cnn_3:0 with name CNN/b_cnn_3
Saving variable lm/CNN_proj/W_proj:0 with name CNN_proj/W_proj
Saving variable lm/CNN_proj/b_proj:0 with name CNN_proj/b_proj
Saving variable lm/CNN_high_0/W_carry:0 with name CNN_high_0/W_carry
Saving variable lm/CNN_high_0/b_carry:0 with name CNN_high_0/b_carry
Saving variable lm/CNN_high_0/W_transform:0 with name CNN_high_0/W_transform
Saving variable lm/CNN_high_0/b_transform:0 with name CNN_high_0/b_tra

In [32]:
!nvidia-smi

Tue Jun 30 12:40:00 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.100      Driver Version: 440.100      CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  GeForce MX150       Off  | 00000000:01:00.0 Off |                  N/A |
| N/A   63C    P0    N/A /  N/A |    234MiB /  2002MiB |      9%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  